# Визуализация BERT

Для визуализации работы модели будут использоваться два метода: 1) визуализация механизма внимания в каждом слое и каждой голове энкодера; 2) интерпретация предсказаний модели с помощью метода интергрированных градиентов.

Визуализируем модель BERT, базовую модель, которая в то же время является наилучшей.

In [5]:
#! pip install bertviz

In [1]:
from bertviz import model_view, head_view
import wandb
from transformers import AutoTokenizer, AutoModelForSequenceClassification
import warnings
import torch

warnings.filterwarnings("ignore")

In [2]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
device

device(type='cuda', index=0)

In [3]:
run = wandb.init()
artifact = run.use_artifact('sava_ml/hw-nlp/baseline38:v1', type='model')
artifact_dir = artifact.download()

wandb: Currently logged in as: sava_ml. Use `wandb login --relogin` to force relogin


wandb: Downloading large artifact baseline38:v1, 680.37MB. 3 files... Done. 0:0:0.0


In [4]:
tokenizer = AutoTokenizer.from_pretrained("sberbank-ai/ruBert-base")
model = AutoModelForSequenceClassification.from_pretrained("artifacts/baseline38:v1", 
                                                           output_attentions=True,
                                                          output_hidden_states=True).to(device)

In [5]:
input_text = "И таким образом, в взаимных поклепах шло время, покуда мои миллионы не очутились в руках Прокопа."

## Визуализация механизма внимания с помощью bertviz

Визуализация я помощью этой библиотеки хорошо работает только для довольно коротких входных последовательностей, поэтому будем визуализировать модель на небольшом отрывке.

In [6]:
inputs = tokenizer.encode(input_text, return_tensors='pt')  # Tokenize input text
outputs = model(inputs.to(device))  # Run model
attention = outputs.attentions  # Retrieve attention from model outputs
tokens = tokenizer.convert_ids_to_tokens(inputs[0])  # Convert input ids to token strings
model_view(attention, tokens)  # Display model view

<IPython.core.display.Javascript object>

In [7]:
last_hidden_states = outputs.hidden_states[-1]
last_hidden_states.size()

torch.Size([1, 24, 768])

In [8]:
head_view(attention, tokens)

<IPython.core.display.Javascript object>

## Интерпретация предсказаний модели с помощью Captum

Для вычисления вклада каждого токена в итоговую вероятность класса, может быть использован метод интегральных градиентов. 

https://towardsdatascience.com/interpreting-the-prediction-of-bert-model-for-text-classification-5ab09f8ef074

In [9]:
import torch
from transformers import AutoTokenizer, AutoModelForSequenceClassification
import captum

In [10]:
tokenizer = AutoTokenizer.from_pretrained("sberbank-ai/ruBert-base")
model = AutoModelForSequenceClassification.from_pretrained("artifacts/baseline38:v1").to(device)
model.eval()

BertForSequenceClassification(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(120138, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0): BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12, elemen

In [11]:
wr2ids = model.config.id2label

In [12]:
# Define model output
def model_output(inputs, model=model):
    return model(inputs).logits

# Define model input
model_input = model.bert.embeddings

In [13]:
from captum.attr import LayerIntegratedGradients

lig = LayerIntegratedGradients(model_output, model_input)

In [14]:
def construct_input_and_baseline(tokenizer, text):

    max_length = 510
    baseline_token_id = tokenizer.pad_token_id 
    sep_token_id = tokenizer.sep_token_id 
    cls_token_id = tokenizer.cls_token_id 

    text_ids = tokenizer.encode(text, max_length=max_length, truncation=True, add_special_tokens=False)
   
    input_ids = [cls_token_id] + text_ids + [sep_token_id]
    token_list = tokenizer.convert_ids_to_tokens(input_ids)

    baseline_input_ids = [cls_token_id] + [baseline_token_id] * len(text_ids) + [sep_token_id]
    return torch.tensor([input_ids], device='cpu'), torch.tensor([baseline_input_ids], device='cpu'), token_list

text = 'Мне больше не хотелось спать'
input_ids, baseline_input_ids, all_tokens = construct_input_and_baseline(tokenizer, text)

print(f'original text: {input_ids}')
print(f'baseline text: {baseline_input_ids}')


original text: tensor([[ 101, 1098, 1344,  672, 4533, 8588,  102]])
baseline text: tensor([[101,   0,   0,   0,   0,   0, 102]])


In [15]:
attributions, delta = lig.attribute(inputs= input_ids.cuda(),
                                    baselines= baseline_input_ids.cuda(),
                                    target=34,
                                    return_convergence_delta=True,
                                    internal_batch_size=1)
print(attributions.size())

torch.Size([1, 7, 768])


In [16]:
def summarize_attributions(attributions):

    attributions = attributions.sum(dim=-1).squeeze(0)
    attributions = attributions / torch.norm(attributions)
    
    return attributions

attributions_sum = summarize_attributions(attributions.cuda())
print(attributions_sum.size())

torch.Size([7])


In [17]:
from captum.attr import visualization as viz

score_vis = viz.VisualizationDataRecord(
                        word_attributions = attributions_sum.cuda(),
                        pred_prob = torch.max(model(input_ids.cuda())[0]),
                        pred_class = torch.argmax(model(input_ids.cuda())[0]).cpu().numpy(),
                        true_class = 1,
                        attr_class = text,
                        attr_score = attributions_sum.sum(),       
                        raw_input_ids = all_tokens,
                        convergence_score = delta)

viz.visualize_text([score_vis])

In [18]:
def interpret_text(tokenizer, model, text, true_class, output_idx=0):

    input_ids, baseline_input_ids, all_tokens = construct_input_and_baseline(tokenizer, text)
    attributions, delta = lig.attribute(inputs= input_ids.cuda(),
                                    baselines= baseline_input_ids.cuda(),
                                    target=true_class,
                                    return_convergence_delta=True,
                                    internal_batch_size=1
                                    )
    attributions_sum = summarize_attributions(attributions)

    score_vis = viz.VisualizationDataRecord(
                        word_attributions = attributions_sum.cuda(),
                        pred_prob = torch.max(model(input_ids.cuda())[output_idx]),
                        pred_class = torch.argmax(model(input_ids.cuda())[output_idx]).cpu().numpy(),
                        true_class = true_class,
                        attr_class = text,
                        attr_score = attributions_sum.sum(),       
                        raw_input_ids = all_tokens,
                        convergence_score = delta)


    viz.visualize_text([score_vis])

In [19]:
text = """И таким образом, в взаимных поклепах шло время, покуда мои миллионы не очутились в руках Прокопа.
Итак, сестрицы сидели в гостиной усадьбы Проплеванной и толковали. Взаимное горе соединило их, но поводы для взаимной ненависти чувствовались еще живее. Для каждой каждая представлялась единственною причиной обманутых надежд и случившегося разорения. Если бы не Машенькины интриги братец наверное отказал бы свой миллион Дашеньке, и наоборот. Хотя же усадьба Проплеванная и принадлежала им несомненно, но большого утешения в этом они не видели. Во-первых, трудно поделить землю: кому отдать просто худородную землю, кому болота и пески? Во-вторых, дом: неминучее дело продать его за бесценок на своз. Отдать Машеньке будет протестовать Дашенька отдать Дашеньке будет протестовать Машенька. Кончится тем, что придется выписать из Петербурга адвоката, который и присудит себе Проплеванную за труды. Следовательно, в будущем виделись только ссоры, утучнение адвоката и бесконечное, безвыходное галдение. И куда делся этот миллион! Вот кабы он был налицо, так тогда, точно, поделить было бы не трудно! Вот вам, Марья Ивановна, пятьсот тысяч, а вот вам, Дарья Ивановна, пятьсот тысяч. Это была такая светлая, такая лучезарная возможность, что на ней сестрицы позабывали даже о взаимной вражде своей.
 Сам! сам перед отъездом в Петербург говорил: миллиона, говорит, добром поделить не хотите! восклицает сестрица Марья Ивановна и от волнения даже вскакивает с места и грозится куда-то в пространство кулаком.
 Сама собственными ушами слышала, как говорил: миллиона, говорит, добром поделить не хотите! вторит с невольным увлечением сестрица Дарья Ивановна.
Фофочка, Лелечка, Нисочка, Аннинька пожимают плечиками и, шепелявя на институтский манер, произносят:
 Это ужасно! Это уж бог знает что!
 И куда этот миллион девался!
 Точно в прорву какую этот миллион провалился!
 То есть руку на отсеченье отдаю, что Прокопка-мерзавец его украл!
 Он, он, он! Кому другому украсть, как не ему, мерзавцу!
 Сказывают, наш-то пьяница так и не расставался с ним в последнее время!"""
true_class = 14
interpret_text(tokenizer, model, text, true_class)

## https://github.com/interpretml/interpret-text Библиотека для интерпретации NLP моделей